## Example Dask Workflow

In [ ]:
from pathlib import Path
from rc_gpfs import compute

In [ ]:
with_cuda=True
manager = compute.start_local_cluster(
    with_cuda, 
    threads_per_worker=10,
    local_directory='/scratch/local',
    rmm_pool_size='70 GiB',
    rmm_managed_memory=True,
    pre_import='cudf,rmm')

Cluster settings:

- `threads_per_worker`: start 10 threads in all available GPUs
- `local_directory`: local working directory for dask worker processes
- `rmm_pool_size`: initialize a 70 GiB memory pool to greatly reduce the number of memory allocation requests during work. If needed, dask can still utilize up to the maximum VRAM, this is just an initial allocation
- `rmm_managed_memory`: greatly improves out-of-memory performance
- `pre_import`: pre-load workers with the given libraries

### Dask Dashboard
If you're on the same network as the compute node (either VPN or sshuttle), you can access the dask dashboard in your browser by going to `<node_ip>:8787`. Jobs on `c0241` will have a dashboard at `172.20.201.241:8787`. You can print the link using the `dashboard_link` property as well, but that will most likely show `127.0.0.1` as the IP which will not work.

In [ ]:
manager.dashboard_link

In [ ]:
! hostname --ip-address

It's advised to have the dashboard available, especially when using methods like `persist()` that look like they have completed successfully but are still running computation in the background

### Shutdown Cluster
It's imperative to shut down the cluster when you're done working. There have been a number of instances where I've restarted the kernel in the middle of a dask compute task where the worker processes could not be successfully killed. This caused the dask watchdog process to timeout which caused NHC to put the node into a drain state. Load increased consistently until the node became unresponsive and had to be rebooted. Before ending your job, call `manager.shutdown()` to close both the dask client and cluster objects.

In [ ]:
#manager.shutdown()

## Dask Analysis

This setup assumes you're using a LocalCUDACluster and so sets the default dataframe backend to `cudf` instead of `pandas`. Remember that every partition is a `cudf.DataFrame` which is mostly compatible with a pandas-style workflow but not always. A common issue is when trying to do anything semi-complicated with datetimes, like cutting into groups. It's generally better to convert those to unix timestamps first (ints) and work from there.

In [ ]:
import dask.dataframe as dd
import dask
dask.config.set({'dataframe.backend':'cudf'})

This example also uses one of the flat parquet datasets from a single GPFS policy run, but can be extended to the hive structure with very minor modifications

### Dataframe Indexing

If you're using the flat parquet, it's highly advised to not set an index after setting up the dataframe unless the `path` column is excluded from the dataset. This causes a large shuffle that must be done mostly in-memory, and the `path` column alone can exceed 80 GB in `data-project` GPFS logs. This can be worked around by reading just a few columns and setting up managed memory (`rmm`) in the cluster options which was done at the beginning of the notebook. This allows most compute to take place, but I wouldn't depend on it for everything.

If you need a dataset that has already been indexed by path, use the hive dataset versions instead. Those are found in `/data/rc/gpfs-policy/data/gpfs-hive/{data-project,data-user,scratch}`. These have not all been computed yet though so a desired dataset may be unavailable.

### Example: Arranging Files into Groups By Similar Size

In [ ]:
gpfs_ds = Path('/data/rc/gpfs-policy/data/list-policy_data-project_list-path-external_slurm-30555647_2024-11-16T00:00:12')
ddf = dd.read_parquet(gpfs_ds.joinpath('parquet'),columns=['path','size'])

In [ ]:
# Set the index to be the path, performing a sort and shuffle across partitions. Persist this into distributed memory 
# since this process takes a while. persist will say everything is completed within a few minutes, but there's still 
# compute happening in the background. This is normal and the intended behavior of persist. If another cell is run 
# while persist computation is still happening, that cell will wait until persist completes before starting, but the 
# jupyter cell timer will start, making it look like the following computation is taking longer than it should
ddf = ddf.set_index('path').persist()

In [ ]:
# Check per-partition in-memory usage. The index is included by default, deep gets us a more accurate measure since the 
# path strings are so long
mem = ddf.memory_usage_per_partition(deep=True).compute()

In [ ]:
print(f"Total in-memory VRAM used by 'path' and 'size' columns: {mem.divide(1024**3).sum().round(2)} GiB")

In [ ]:
# Setting the index causes divisions between partitions to become know since all of the data are sorted. Notice that 
# partitions are not automatically sized by tld (i.e. one tld per partition) and so some partitions will contain 
# multiple tld values
ddf.divisions

In [ ]:
def split_into_groups(df, threshold = 100*(1024**3), partition_info=None):
    df = df.sort_values('size')
    df['cumsum'] = df['size'].cumsum()
    df['group'] = (df['cumsum'] // threshold).astype(str)
    if partition_info is not None:
        partition_number = str(partition_info.get('number'))
    else:
        partition_number = 'nan'

    df['group'] = df['group'].str.insert(-1,f'_{partition_number}')
    return df[['size','group']]

In [ ]:
# Split files into groups by size where each group is 100 GiB at most. Any files larger than the cutoff are separated 
# into their own group.
ddf = ddf.map_partitions(split_into_groups)

In [ ]:
out_path = gpfs_ds.joinpath('file_grps')
out_path.mkdir(exist_ok=True)

In [ ]:
ddf.to_parquet(out_path)

### Example: Aggregate Data By File Size

In [ ]:
import cudf

In [ ]:
ddf = dd.read_parquet(gpfs_ds.joinpath('parquet'),columns=['path','size'])

In [ ]:
bins = [1024**n for n in range(0,6)]
labels = ['1B-1kiB','1kiB-1MiB','1MiB-1GiB','1GiB-1TiB','>1TiB']

In [ ]:
ddf['size_group'] = ddf['size'].map_partitions(lambda x: cudf.cut(x,bins=bins,labels=labels,right=False))

In [ ]:
df_agg = ddf.groupby('size_group',observed=True)['size'].agg(['count','sum']).compute().to_pandas()

In [ ]:
df_agg.columns = ['file_count','bytes']

In [ ]:
df_agg = df_agg.reset_index()

In [ ]:
df_agg['size_group'] = df_agg['size_group'].astype('category').cat.set_categories(labels,ordered=True)
df_agg = df_agg.sort_values('size_group')

In [ ]:
from rc_gpfs.report import plotting

In [ ]:
exp,unit = plotting.choose_appropriate_storage_unit(df_agg['bytes'])
df_agg[unit] = df_agg['bytes']/(1024**exp)

In [ ]:
df_agg[['file_count_cum',f'{unit}_cum']] = df_agg[['file_count',unit]].cumsum()
df_agg[[unit,f'{unit}_cum']] = df_agg[[unit,f'{unit}_cum']].round(3)

In [ ]:
f1 = plotting.pareto_chart(df_agg,x='size_group',y=unit,
                           title="Storage Used By File Size", xlabel='Size Group',ylabel='Size (TiB)')
f1.show()

In [ ]:
f2 = plotting.pareto_chart(df_agg, x='size_group', y='file_count',
                           title="File Count By File Size", xlabel='Size Group',ylabel='Count')
f2.show()